# ISAAC Athletics Analytics - Marginal Percent Change Interactive Plot Jupyter Notebook

### This Jupyter Notebook contains the Python script to create an Interactive Plot to display the Marginal Percent Change of the 5 metrics (Top 4 predictors + mRSI) for any athlete available in the dataset

### 1. Importing libraries

In [1]:
import os
import os.path
import pandas as pd
import numpy as np
import plotly
import plotly.express as px
import plotly.graph_objects as go
from datetime import datetime
import base64

### 2. Importing data

In [2]:
# Define the directory and file path for the dataset
datadir = "data/tidy_data"
# Load the dataset into a DataFrame
data = pd.read_csv(os.path.join(datadir, "new_jump_data.csv"))

# Create a binary variable 'injury_log' to indicate injury occurrence:
# 1 for rows where 'injury_type' is not NaN (indicating an injury), and 0 otherwise
data["injury_log"] = data["injury_type"].notna().astype(int)

marginal_df = data[[
    "athlete_code", "Date", "mRSI", "Peak Braking Velocity", "Peak Propulsive Force", "Avg. Braking Power", "Peak Braking Force", "injury_log"
]]

def date_coversion(date):
    # Check if the date is a valid string before processing
    if isinstance(date, str):
        try:
            date_object = datetime.strptime(date, '%m-%d-%Y')
            iso_format_date = date_object.strftime('%Y-%m-%d')
            return iso_format_date
        except ValueError:
            return None  # Return None if the date format is incorrect
    return date  # If it's not a string, return the value as is (e.g., NaN or float)

# Changing date formatting
marginal_df["Date"] = marginal_df["Date"].str.replace("/", "-").apply(date_coversion)# Convert to datetime format (this will handle invalid or missing dates gracefully)
marginal_df["Date"] = pd.to_datetime(marginal_df["Date"])

C:\Users\Admin\AppData\Local\Temp\ipykernel_79664\3910937766.py:26: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  marginal_df["Date"] = marginal_df["Date"].str.replace("/", "-").apply(date_coversion)# Convert to datetime format (this will handle invalid or missing dates gracefully)
C:\Users\Admin\AppData\Local\Temp\ipykernel_79664\3910937766.py:27: SettingWithCopyWarning: 
A value is trying to be set on a copy of a slice from a DataFrame.
Try using .loc[row_indexer,col_indexer] = value instead

See the caveats in the documentation: https://pandas.pydata.org/pandas-docs/stable/user_guide/indexing.html#returning-a-view-versus-a-copy
  marginal_df["Date"] = pd.to_datetime(marginal_df["Date"])


### 3. Aggregating data

In [3]:
marginal_df = data[[
    "athlete_code", "Date", "mRSI", "Peak Braking Velocity", "Peak Propulsive Force", "Avg. Braking Power", "Peak Braking Force", "injury_log"
]]

marginal_data = (
    marginal_df.groupby(['athlete_code', 'Date'], as_index=False)
    .agg(
        Avg_mRSI=('mRSI', 'mean'),
        Avg_Peak_Braking_Velocity=('Peak Braking Velocity', 'mean'),
        Avg_Peak_Propulsive_Force=('Peak Propulsive Force', 'mean'),
        Avg_Avg_Braking_Power=('Avg. Braking Power', 'mean'),
        Avg_Peak_Braking_Force=('Peak Braking Force', 'mean')
    )
    .sort_values(by=['athlete_code', 'Date'], ascending=[True, True])  # Sort by athlete_code and Date
)

# Calculate the percentage change for each column (mRSI and others)
marginal_data['mRSI'] = marginal_data['Avg_mRSI'].pct_change()
marginal_data['Peak_Braking_Velocity'] = marginal_data['Avg_Peak_Braking_Velocity'].pct_change()
marginal_data['Peak_Propulsive_Force'] = marginal_data['Avg_Peak_Propulsive_Force'].pct_change()
marginal_data['Avg_Braking_Power'] = marginal_data['Avg_Avg_Braking_Power'].pct_change()
marginal_data['Peak_Braking_Force'] = marginal_data['Avg_Peak_Braking_Force'].pct_change()

marginal_data['Date'] = marginal_data['Date'].str.replace("/", "-").apply(date_coversion)
marginal_data["Date"] = pd.to_datetime(marginal_data["Date"])
marginal_data = marginal_data.sort_values(by=['athlete_code', 'Date'], ascending=[True, True])

### 4. Creating the interactive plot

In [4]:
# Function to create the plot for a specific athlete and selected metric
def create_plot(athlete_code, metric='mRSI_marginal_change', filename="athlete_plot.html"):
    # Filter data for the selected athlete
    marginal_data_single = marginal_data[marginal_data['athlete_code'] == athlete_code]

    # Create Plotly figure
    fig = go.Figure()

    # Add line plot (black line)
    fig.add_trace(go.Scatter(
        x=marginal_data_single['Date'],
        y=marginal_data_single[metric],
        mode='lines',
        line=dict(color='black'),
        name='Line'
    ))

    # Add scatter plot (red points)
    fig.add_trace(go.Scatter(
        x=marginal_data_single['Date'],
        y=marginal_data_single[metric],
        mode='markers',
        marker=dict(color='red', size=8),
        name='Points'
    ))

    # Add logo image (optional)
    with open("logo/horizontal_logo.png", "rb") as img:
        encoded_image = base64.b64encode(img.read()).decode()

    fig.add_layout_image(
        dict(
            source=f"data:image/png;base64,{encoded_image}",
            xref="paper", yref="paper",
            x=0.99, y=1.05,
            sizex=0.15, sizey=0.15,
            xanchor="right", yanchor="bottom"
        )
    )

    # Add title and labels
    fig.update_layout(
        font_family="Helvetica",
        width=1600,
        height=900,
        title=dict(
            text=f"<b>Marginal Percentage Change in {metric.replace('_', ' ').title()} for Athlete {athlete_code}</b>",
            font=dict(size=28, family="Helvetica"),
            x=0.018,
            y = 0.93
        ),
        xaxis_title="Date",
        yaxis_title=f"Marginal Percentage Change in {metric.replace('_', ' ').title()}",
        xaxis=dict(tickangle=45),
        annotations=[
            dict(
                x=-0.037,
                y=1.065,
                text="Choose metric here:",
                showarrow=False,
                font=dict(size=20, family="Helvetica"),
                xref="paper",
                yref="paper",
                align="left"
            ),
            dict(
                x=0.37,
                y=1.065,
                text="Choose athlete here:",
                showarrow=False,
                font=dict(size=20, family="Helvetica"),
                xref="paper",
                yref="paper",
                align="left"
            )
        ],
        template="plotly_white",
        updatemenus=[
            dict(
                buttons=[
                    # Add buttons for each athlete
                    dict(
                        args=[{"x": [marginal_data[marginal_data['athlete_code'] == athlete]['Date']],
                               "y": [marginal_data[marginal_data['athlete_code'] == athlete][metric]]},
                              {"title": f"<b>Marginal Percentage Change in {metric.replace('_', ' ').title()} for Athlete {athlete}</b>"}],
                        label=athlete,
                        method="update"
                    ) for athlete in marginal_data['athlete_code'].unique()
                ],
                direction="down",
                showactive=True,
                x=0.442,
                xanchor="left",
                y=1.15,
                yanchor="top",
                pad={"t": 50}  # Space for the dropdown
            ),
            # Dropdown for metric selection
            dict(
                buttons=[
                    dict(
                        args=[{"y": [marginal_data[marginal_data['athlete_code'] == athlete_code][metric]]},
                              {"title": f"<b>Marginal Percentage Change in {metric.replace('_', ' ').title()} for Athlete {athlete_code}</b>"}],
                        label=metric.replace('_', ' ').title(),
                        method="update"
                    ) for metric in [
                        'mRSI',
                        'Peak_Braking_Velocity',
                        'Peak_Propulsive_Force',
                        'Avg_Braking_Power',
                        'Peak_Braking_Force'
                    ]
                ],
                direction="down",
                showactive=True,
                x=0.1,
                xanchor="left",
                y=1.225,
                yanchor="top",
                pad={"t": 100}  # Space for the dropdown
            )
        ]
    )

    # Save the plot as an HTML file
    fig.write_html(filename)

    # Show the plot
    fig.show()

# List of available athlete codes
athlete_codes = marginal_data['athlete_code'].unique()

# Create the initial plot for the first athlete and default metric
create_plot(athlete_codes[0], metric='mRSI', filename="test_athlete_plot.html")


In [12]:
# Sample DataFrame for demonstration
athlete_codes = marginal_data['athlete_code'].unique()
metrics = ['mRSI', 'Peak_Braking_Velocity', 'Peak_Propulsive_Force', 'Avg_Braking_Power', 'Peak_Braking_Force']
# Function to create the figure
def create_figure(selected_athlete, metric='mRSI_marginal_change', filename="athlete_plot.html"):
    # Filter data for the selected athlete
    athlete_data = marginal_data[marginal_data['athlete_code'] == selected_athlete]
    
    # Create figure
    fig = go.Figure()

    # Add traces for each metric
    for metric in metrics:
        fig.add_trace(go.Scatter(
            x=athlete_data['Date'],
            y=athlete_data[metric],
            name=metric,
            visible='legendonly'  # Default visibility to legend only
        ))

    # Update layout
    fig.update_layout(
        autosize=False,
        width=1600,
        height=900,
        title=dict(
            text=f"<b>Metrics for Athlete {selected_athlete}</b>",
            font=dict(size=30, family="Helvetica")
        ),
        xaxis=dict(
            title="<i>Date</i>",
            titlefont=dict(size=20, family="Helvetica")
        ),
        yaxis=dict(
            title="<i>Value</i>",
            titlefont=dict(size=20, family="Helvetica")
        ),
        updatemenus=[
            # Metric Toggle Buttons
            dict(
                type="buttons",
                direction="down",
                buttons=[
                    dict(
                        label="Toggle All",
                        method="update",
                        args=[{"visible": [True] * len(metrics)}],
                        args2=[{"visible": ['legendonly'] * len(metrics)}]
                    ),
                    dict(
                        label="Toggle Off",
                        method="update",
                        args=[{"visible": ['legendonly'] * len(metrics)}]
                    )
                ],
                font=dict(size=15, family="Helvetica"),
                x=1.05,  # Position to the right of the plot
                y=1.15,
                showactive=True
            ),
            # Dropdown for Athlete Selection
            dict(
                buttons=[
                    dict(
                        label=athlete,
                        method="update",
                        args=[
                            # Update x and y data for all metrics
                            {
                                "x": [marginal_data[marginal_data['athlete_code'] == athlete]['Date']] * len(metrics),
                                "y": [
                                    marginal_data[marginal_data['athlete_code'] == athlete][metric]
                                    for metric in metrics
                                ],
                                # Update the title dynamically
                                "title.text": f"<b>Metrics for Athlete {athlete}</b>"
                            }
                        ]
                    ) for athlete in athlete_codes
                ],
                type="dropdown",
                direction="down",
                x=0.17,
                xanchor="right",
                y=1.15,
                yanchor="top",
                font=dict(size=15, family="Helvetica"),
                showactive=True
            )
        ],
        template="plotly_white"
    )
    # Save and show the plot
    fig.write_html("athlete_metrics.html")
    fig.show()

create_figure(athlete_codes[0], metric='mRSI', filename="test_athlete_plot.html")

In [63]:
# List of available metrics
metrics = ['mRSI', 'Peak_Braking_Velocity', 'Peak_Propulsive_Force', 'Avg_Braking_Power', 'Peak_Braking_Force']

# Function to create the plot for a specific athlete
def create_plot(athlete_code, filename="athlete_plot.html"):
    # Filter data for the selected athlete
    marginal_data_single = marginal_data[marginal_data['athlete_code'] == athlete_code]

    # Create Plotly figure
    fig = go.Figure()

    # Add traces for each metric
    for metric in metrics:
        fig.add_trace(go.Scatter(
            x=marginal_data_single['Date'],
            y=marginal_data_single[metric],
            mode='lines+markers',
            name=metric,
            visible=True  # Default to visible
        ))

    # Add logo image (optional)
    with open("logo/horizontal_logo.png", "rb") as img:
        encoded_image = base64.b64encode(img.read()).decode()

    fig.add_layout_image(
        dict(
            source=f"data:image/png;base64,{encoded_image}",
            xref="paper", yref="paper",
            x=0.99, y=1.05,
            sizex=0.15, sizey=0.15,
            xanchor="right", yanchor="bottom"
        )
    )

    # Update layout with dropdowns and checkboxes
    fig.update_layout(
        font_family="Helvetica",
        width=1600,
        height=900,
        title=dict(
            text=f"<b>Marginal Percent Change of Metrics for Athlete {athlete_code}</b>",
            font=dict(size=28, family="Helvetica"),
            x=0.019,
            y=0.97
        ),
        xaxis_title="Date",
        yaxis_title="Metric Value",
        xaxis=dict(tickangle=45),
        annotations=[
            dict(
                x=-0.038,
                y=1.065,
                text="Choose athlete here:",
                showarrow=False,
                font=dict(size=20, family="Helvetica"),
                xref="paper",
                yref="paper",
                align="left"
            )
        ],
        template="plotly_white",
        updatemenus=[
            # Dropdown for athlete selection
            dict(
                buttons=[
                    dict(
                        args=[
                            {"x": [marginal_data[marginal_data['athlete_code'] == athlete]['Date']] * len(metrics),
                             "y": [
                                 marginal_data[marginal_data['athlete_code'] == athlete][metric]
                                 for metric in metrics
                             ]},
                            {"title.text": f"<b>Marginal Percent Change of Metrics  for Athlete {athlete}</b>"}
                        ],
                        label=athlete,
                        method="update"
                    ) for athlete in marginal_data['athlete_code'].unique()
                ],
                direction="down",
                showactive=True,
                x=0.11,
                xanchor="left",
                y=1.14,
                yanchor="top",
                pad={"t": 50}  # Space for the dropdown
            ),
            dict(
            type="buttons",
            direction="down",
            buttons=list([
                dict(
                    label="Toggle All",
                    visible = True,
                    args = [{'visible':True}],
                    args2 = [{'visible':'legendonly'}]
                ),
                dict(
                    label="Toggle Off",
                    visible = True,
                    args = [{'visible':'legendonly'}]
                ),
            ]),
            font = dict(
                size=15,
                family = "Helvetica" 
            ),
            x=1.02,
            xanchor="left",
            y=0.85,
            yanchor="top",
        ),
        ]
    )

    # Save the plot as an HTML file
    fig.write_html(filename)

    # Show the plot
    fig.show()

# List of available athlete codes
athlete_codes = marginal_data['athlete_code'].unique()

# Create the initial plot for the first athlete
create_plot(athlete_codes[0], filename="test_athlete_plot.html")
